In [1]:
import pandas as pd
import glob
import re
# from collections import defaultdict
from itertools import combinations
import os

In [2]:
query="house predictions"


# Helper: Standardize column names
def normalize(col):
    return re.sub(r'[^a-z0-9]', '', col.lower())

# Step 1: Read CSVs
csv_files = glob.glob("downloads/covid 19/*.csv")
dfs = [pd.read_csv(f) for f in csv_files]

# Step 2: Store normalized-to-original column mappings
normalized_cols = []
orig_col_maps = []

for df in dfs:
    norm_to_orig = {}
    norm_cols = []
    for col in df.columns:
        norm = normalize(col)
        norm_cols.append(norm)
        norm_to_orig[norm] = col
    normalized_cols.append(set(norm_cols))
    orig_col_maps.append(norm_to_orig)


# normalized_cols,orig_col_maps

In [ ]:
from rapidfuzz import process, fuzz

def get_fuzzy_common_columns(cols_list, threshold=85):
    """
    Given a list of sets of column names (normalized),
    return the set of column names that are 'fuzzy common'
    across all lists.
    """
    # Start with columns from the first dataset
    base = cols_list[0]
    common = set()

    for col in base:
        match_all = True
        for other in cols_list[1:]:
            match, score, _ = process.extractOne(col, other, scorer=fuzz.token_sort_ratio)
            if score < threshold:
                match_all = False
                break
        if match_all:
            common.add(col)
    return common


In [ ]:
max_common = set()
best_combo = []

for i in range(2, len(dfs) + 1):
    for combo in combinations(range(len(dfs)), i):
        common = set.intersection(*[normalized_cols[i] for i in combo])
        # some=[normalized_cols[i] for i in combo]
        # print(some)
        if len(common) > len(max_common):
            max_common = common
            best_combo = combo

max_common,best_combo

[{'max', 'prcp', 'min', 'lat', 'long', 'temp', 'provincestate', 'dayfromjanfirst', 'date', 'wdsp', 'fog', 'fatalities', 'ah', 'stp', 'confirmedcases', 'countryregion', 'rh', 'slp', 'dewp', 'id'}, {'max', 'prcp', 'min', 'lat', 'long', 'temp', 'provincestate', 'dayfromjanfirst', 'date', 'wdsp', 'fog', 'fatalities', 'ah', 'stp', 'countryprovince', 'confirmedcases', 'countryregion', 'rh', 'slp', 'dewp', 'id'}]
[{'max', 'prcp', 'min', 'lat', 'long', 'temp', 'provincestate', 'dayfromjanfirst', 'date', 'wdsp', 'fog', 'fatalities', 'ah', 'stp', 'confirmedcases', 'countryregion', 'rh', 'slp', 'dewp', 'id'}, {'cumulativecases', 'datereported', 'newdeaths', 'countrycode', 'cumulativedeaths', 'whoregion', 'country', 'newcases'}]
[{'max', 'prcp', 'min', 'lat', 'long', 'temp', 'provincestate', 'dayfromjanfirst', 'date', 'wdsp', 'fog', 'fatalities', 'ah', 'stp', 'countryprovince', 'confirmedcases', 'countryregion', 'rh', 'slp', 'dewp', 'id'}, {'cumulativecases', 'datereported', 'newdeaths', 'countryc

(set(), [])

In [17]:
aligned_dfs = []
for idx in best_combo:
    df = dfs[idx]
    norm_to_orig = orig_col_maps[idx]
    selected_cols = [norm_to_orig[col] for col in max_common]
    df_subset = df[selected_cols].copy()
    df_subset.columns = [col for col in max_common]  # unify column names
    aligned_dfs.append(df_subset)

# Step 5: Combine
combined_df = pd.concat(aligned_dfs, ignore_index=True)

In [9]:
for df in dfs:
    print(df.index.size)

17892
24414
54960


In [11]:
for i in range(2, len(dfs) + 1):
    for combo in combinations(range(len(dfs)), i):
        counts=[dfs[i].index.size for i in combo]
        print(counts)

[17892, 24414]
[17892, 54960]
[24414, 54960]
[17892, 24414, 54960]


In [12]:
maxCount=0
idx=-1
for i in range(len(dfs)):
    if dfs[i].index.size > maxCount:
        maxCount=dfs[i].index.size
        idx=i

maxCount,idx

(54960, 2)

In [18]:
combined_df.index.size,maxCount

(42306, 54960)

In [20]:
str="hello and "
str[:5]

'hello'

In [2]:
import pandas as pd

df=pd.read_csv("downloads/wine quality prediction/redwine.csv")
df.head()

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0            7.4              0.70         0.00             1.9      0.076   
1            7.8              0.88         0.00             2.6      0.098   
2            7.8              0.76         0.04             2.3      0.092   
3           11.2              0.28         0.56             1.9      0.075   
4            7.4              0.70         0.00             1.9      0.076   

   free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                 11.0                  34.0   0.9978  3.51       0.56   
1                 25.0                  67.0   0.9968  3.20       0.68   
2                 15.0                  54.0   0.9970  3.26       0.65   
3                 17.0                  60.0   0.9980  3.16       0.58   
4                 11.0                  34.0   0.9978  3.51       0.56   

   alcohol  quality  
0      9.4        5  
1      9.8        5  
2      9.8        5  
3      9.8        6  
4      9.4        5

In [9]:
import glob
csv_files = glob.glob("downloads/"+"wine quality prediction"+"/*.csv")
csv_files[0]

'downloads/wine quality prediction\\redwine.csv'

In [11]:
df=pd.read_csv(csv_files[0])
df.head()

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0            7.4              0.70         0.00             1.9      0.076   
1            7.8              0.88         0.00             2.6      0.098   
2            7.8              0.76         0.04             2.3      0.092   
3           11.2              0.28         0.56             1.9      0.075   
4            7.4              0.70         0.00             1.9      0.076   

   free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                 11.0                  34.0   0.9978  3.51       0.56   
1                 25.0                  67.0   0.9968  3.20       0.68   
2                 15.0                  54.0   0.9970  3.26       0.65   
3                 17.0                  60.0   0.9980  3.16       0.58   
4                 11.0                  34.0   0.9978  3.51       0.56   

   alcohol  quality  
0      9.4        5  
1      9.8        5  
2      9.8        5  
3      9.8        6  
4      9.4        5

In [ ]:
import os
newName=os.path.basename(csv_files[0]).lower().split(".")[0]
query="wine quality prediction"

words=set(query.lower().split())

for word in words:
    if word in newName:
        newName=newName.replace(word,"")

df['label']=newName

df.head()

fixed acidity  volatile acidity  citric acid  residual sugar  chlorides  \
0            7.4              0.70         0.00             1.9      0.076   
1            7.8              0.88         0.00             2.6      0.098   
2            7.8              0.76         0.04             2.3      0.092   
3           11.2              0.28         0.56             1.9      0.075   
4            7.4              0.70         0.00             1.9      0.076   

   free sulfur dioxide  total sulfur dioxide  density    pH  sulphates  \
0                 11.0                  34.0   0.9978  3.51       0.56   
1                 25.0                  67.0   0.9968  3.20       0.68   
2                 15.0                  54.0   0.9970  3.26       0.65   
3                 17.0                  60.0   0.9980  3.16       0.58   
4                 11.0                  34.0   0.9978  3.51       0.56   

   alcohol  quality label  
0      9.4        5   red  
1      9.8        5   red  
2      9.8        5   red  
3      9.8        6   red  
4      9.4        5   red

In [2]:
import pandas as pd

df=pd.read_csv("final/covid 19.csv")
df.head()

Date_reported Country_code      Country WHO_region  New_cases  \
0    2020-01-05           AF  Afghanistan       EMRO        NaN   
1    2020-01-12           AF  Afghanistan       EMRO        NaN   
2    2020-01-19           AF  Afghanistan       EMRO        NaN   
3    2020-01-26           AF  Afghanistan       EMRO        NaN   
4    2020-02-02           AF  Afghanistan       EMRO        NaN   

   Cumulative_cases  New_deaths  Cumulative_deaths  
0                 0         NaN                  0  
1                 0         NaN                  0  
2                 0         NaN                  0  
3                 0         NaN                  0  
4                 0         NaN                  0

In [3]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 54960 entries, 0 to 54959
Data columns (total 8 columns):
 #   Column             Non-Null Count  Dtype  
---  ------             --------------  -----  
 0   Date_reported      54960 non-null  object 
 1   Country_code       54731 non-null  object 
 2   Country            54960 non-null  object 
 3   WHO_region         50838 non-null  object 
 4   New_cases          38082 non-null  float64
 5   Cumulative_cases   54960 non-null  int64  
 6   New_deaths         24747 non-null  float64
 7   Cumulative_deaths  54960 non-null  int64  
dtypes: float64(2), int64(2), object(4)
memory usage: 3.4+ MB


In [4]:
object_columns = df.dtypes[df.dtypes == 'object'].index.tolist()
object_columns

['Date_reported', 'Country_code', 'Country', 'WHO_region']

In [5]:
import pandas as pd

def one_hot_encode_objects(df):
    object_cols = df.select_dtypes(include='object').columns

    for col in object_cols:
        if "date" in col:
            continue

        # Perform one-hot encoding
        dummies = pd.get_dummies(df[col], prefix=col).astype(int)
        df = pd.concat([df, dummies], axis=1)
        
    df = df.drop(columns=object_cols)
    return df


def preprocessing(query):
    df=pd.read_csv("final/"+query+".csv")
    # print(df.head())
    df=one_hot_encode_objects(df)
    print(df.head())
    
    
preprocessing("covid 19")

   New_cases  Cumulative_cases  New_deaths  Cumulative_deaths  \
0        NaN                 0         NaN                  0   
1        NaN                 0         NaN                  0   
2        NaN                 0         NaN                  0   
3        NaN                 0         NaN                  0   
4        NaN                 0         NaN                  0   

   Date_reported_2020-01-05  Date_reported_2020-01-12  \
0                         1                         0   
1                         0                         1   
2                         0                         0   
3                         0                         0   
4                         0                         0   

   Date_reported_2020-01-19  Date_reported_2020-01-26  \
0                         0                         0   
1                         0                         0   
2                         1                         0   
3                         0           

In [2]:
import pandas as pd

def reduce_csv_to_10_percent(file_path):
    # Read the original CSV
    df = pd.read_csv(file_path)

    # Sample 10% of the rows
    reduced_df = df.sample(frac=0.1, random_state=42)

    # Save back to the original file path, overwriting it
    reduced_df.to_csv(file_path, index=False)
    print(f"Reduced file saved to: {file_path}")

# Example usage
reduce_csv_to_10_percent("final/twitter sentiment analysis.csv")

Reduced file saved to: final/twitter sentiment analysis.csv
